In [1]:
import os

from utils.util_new import *
from train_test import *

In [2]:
MIND_type = 'small'
data_path = "/datasets/"

train_news_file = os.path.join(data_path, 'mind_train', r'news.tsv')
train_behaviors_file = os.path.join(data_path, 'mind_train', r'behaviors.tsv')
valid_news_file = os.path.join(data_path, 'mind_val', r'news.tsv')
valid_behaviors_file = os.path.join(data_path, 'mind_val', r'behaviors.tsv')
knowledge_graph_file = os.path.join(data_path, 'mind_kg', r'wikidata-graph.tsv')
entity_embedding_file = os.path.join(data_path, 'mind_kg', r'entity2vecd100.vec')
relation_embedding_file = os.path.join(data_path, 'mind_kg', r'relation2vecd100.vec')

mind_url, mind_train_dataset, mind_dev_dataset, _ = get_mind_data_set(MIND_type)


In [3]:
import argparse
from parse_config import ConfigParser


parser = argparse.ArgumentParser(description='KRED')

parser.add_argument('-f')


parser.add_argument('-c', '--config', default="./config.json", type=str,
                    help='config file path (default: None)')
parser.add_argument('-r', '--resume', default=None, type=str,
                    help='path to latest checkpoint (default: None)')
parser.add_argument('-d', '--device', default=None, type=str,
                    help='indices of GPUs to enable (default: all)')

config = ConfigParser.from_args(parser)

In [4]:
from utils.cleaner import *
config = cleaner(config)

In [5]:
entity2id_dict = entity_to_id(config, entities_news(config))

In [6]:
entity_embedding = []

In [7]:
entity_embedding.append(np.zeros(config['model']['entity_embedding_dim']))

In [8]:
entity2embedding_dict = {}
entity2embedding_dict, entity_embedding, relation_embedding = construct_embedding_mind(config, entity2id_dict, entity_embedding, entity2embedding_dict)


constructing embedding ...


In [9]:
entity_adj, relation_adj = construct_adj_mind(config, entity2id_dict, entity2embedding_dict)

constructing adjacency matrix ...


In [10]:
entities_not_embedded = set([item for items in entity_adj for item in items]).difference(set(entity2id_dict.values()))
entity2id_dict_not_embedded = id_to_entity(config, entities_not_embedded)
entity2embedding_dict, entity_embedding, relation_embedding = construct_embedding_mind(config, entity2id_dict_not_embedded, entity_embedding, entity2embedding_dict)

# Add the new entities to the dictionary
entity2id_dict.update(entity2id_dict_not_embedded)
# Invert the dictionary
id2entity_dict = {v: k for k, v in entity2id_dict.items()}

constructing embedding ...


In [11]:
for i in range(1, len(entity_adj)):
    for j in range(0, len(entity_adj[i])):
        entity_adj[i][j] = entity2embedding_dict[id2entity_dict[entity_adj[i][j]]]
entity_embedding = torch.FloatTensor(np.array(entity_embedding))
relation_embedding = torch.FloatTensor(np.array(relation_embedding))

In [13]:
embedding_folder=None
news_feature, max_entity_freq, max_entity_pos, max_entity_type = build_news_features_mind(config, entity2embedding_dict, embedding_folder)

# Load the user history
user_history = build_user_history(config)


Load pretrained SentenceTransformer: distilbert-base-nli-stsb-mean-tokens


Downloading:   0%|          | 0.00/345 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/190 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/4.01k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/555 [00:00<?, ?B/s]

...

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

In [14]:
train_data, dev_data = get_user2item_data(config)
vert_train, vert_test = build_vert_data(config)
pop_train, pop_test = build_pop_data(config)
item2item_train, item2item_test = build_item2item_data(config)

{'lifestyle': 0, 'news': 1, 'health': 2, 'weather': 3, 'entertainment': 4, 'autos': 5, 'travel': 6, 'sports': 7, 'foodanddrink': 8, 'tv': 9, 'movies': 10, 'finance': 11, 'video': 12, 'music': 13, 'middleeast': 14, 'kids': 15, 'northamerica': 16}


In [15]:
data_dict = {
    'user_history' : user_history,
    'entity_embedding' : entity_embedding,
    'relation_embedding' : relation_embedding,
    'entity_adj' : entity_adj,
    'relation_adj' : relation_adj,
    'news_feature': news_feature,
    'max_entity_freq':max_entity_freq,
    'max_entity_pos': max_entity_pos,
    'max_entity_type':max_entity_type,
    'train_data': train_data,
    'dev_data':dev_data,
    'vert_train': vert_train,
    'vert_test' : vert_test,
    'pop_train': pop_train,
    'pop_test':pop_test,
    'item2item_train': item2item_train,
    'item2item_test': item2item_test
}

In [17]:
import gzip
import pickle

def save_compressed_pickle(obj, filename):
    with gzip.open(filename, 'wb') as f:
        pickle.dump(obj, f)
save_compressed_pickle(data_dict, 'data_saved.pkl')

In [26]:
if config['trainer']['training_type']  == "multi-task":
    data = user_history, entity_embedding, relation_embedding, entity_adj, relation_adj, news_feature, max_entity_freq, max_entity_pos, max_entity_type, train_data, dev_data, vert_train, vert_test, pop_train, pop_test, item2item_train, item2item_test
elif config['trainer']['task'] == "user2item":
    data = user_history, entity_embedding, relation_embedding, entity_adj, relation_adj, news_feature, max_entity_freq, max_entity_pos, max_entity_type, train_data, dev_data
elif config['trainer']['task'] == "item2item":
    data =  user_history, entity_embedding, relation_embedding, entity_adj, relation_adj, news_feature, max_entity_freq, max_entity_pos, max_entity_type, item2item_train, item2item_test
elif config['trainer']['task'] == "vert_classify":
    data = user_history, entity_embedding, relation_embedding, entity_adj, relation_adj, news_feature, max_entity_freq, max_entity_pos, max_entity_type, vert_train, vert_test
elif config['trainer']['task'] == "pop_predict":
    data = user_history, entity_embedding, relation_embedding, entity_adj, relation_adj, news_feature, max_entity_freq, max_entity_pos, max_entity_type, pop_train, pop_test

In [21]:
epochs = 5
batch_size = 256
train_type = "single_task"
task = "user2item" # task should be within: user2item, item2item, vert_classify, pop_predict

config['trainer']['epochs'] = epochs
config['data_loader']['batch_size'] = batch_size
config['trainer']['training_type'] = train_type
config['trainer']['task'] = task

In [27]:
# Must adapt dict to do the task
if train_type == "single_task":
    single_task_training(config, data)
else:
    multi_task_training(config, data)

model training
Training epoch 0/6 - 0.0
######
 Step: 0, 0.0 
######
all loss: tensor(67.5588, device='cuda:0', grad_fn=<AddBackward0>)
_train_epoch
all loss: tensor(66.1389, device='cuda:0', grad_fn=<AddBackward0>)
_train_epoch
auc socre: 0.6006036726512551
valid_socre
valid_scores
early_stopping
Saving checkpoint: out/saved/models/KRED/1224_012414/checkpoint-model-epoch2.pth ...
epoch % self.save_period
Training epoch 2/6 - 0.3333333333333333
######
 Step: 0, 0.0 
######
all loss: tensor(65.0397, device='cuda:0', grad_fn=<AddBackward0>)
_train_epoch
auc socre: 0.6014684494569537
valid_socre
valid_scores
early_stopping
Saving checkpoint: out/saved/models/KRED/1224_012414/checkpoint-model-epoch3.pth ...
epoch % self.save_period
Training epoch 3/6 - 0.5
######
 Step: 0, 0.0 
######
all loss: tensor(64.2479, device='cuda:0', grad_fn=<AddBackward0>)
_train_epoch
auc socre: 0.5999283206142517
valid_socre
valid_scores
early_stopping
Saving checkpoint: out/saved/models/KRED/1224_012414/check